# Check pnl across trades and positions

* Compare trade pnl between two subgraphs
* Compare position pnl between two subgraphs


In [51]:
import os
from copy import deepcopy
from datetime import datetime
import asyncio
import requests
import pandas as pd
import numpy as np
import json
import sqlite3
from gql import Client, gql
from gql.transport.aiohttp import AIOHTTPTransport
from decimal import Decimal
from dotenv import load_dotenv
import plotly.io as pio
import plotly.express as px

load_dotenv()

pio.renderers.default = 'notebook'


In [52]:
## constants
INFURA_KEY = os.getenv('INFURA_KEY')

# set up sqlite connection
con = sqlite3.connect("../../data/perps.db")


### Run a query

In [53]:
df_position = pd.read_sql_query('SELECT * FROM positions', con)
df_trade = pd.read_sql_query('SELECT * FROM trades', con)
df_stat = pd.read_sql_query('SELECT * FROM stats', con)


In [54]:
# add fields
df_position['netPnl'] = df_position['pnl'] - df_position['feesPaid']
df_trade['netPnl'] = df_trade['pnl'] - df_trade['feesPaid']


## Plot market pnl over time

In [55]:
df_market_pnl = df_trade.sort_values(['asset', 'timestamp'])
df_market_pnl['netPnl'] = df_market_pnl['pnl'] - df_market_pnl['feesPaid']

df_market_pnl['timestamp'] = df_market_pnl['timestamp'].astype(np.int64)
df_market_pnl['pnl'] = df_market_pnl['pnl'].astype(np.float64)
df_market_pnl['netPnl'] = df_market_pnl['netPnl'].astype(np.float64)
df_market_pnl['feesPaid'] = df_market_pnl['feesPaid'].astype(np.float64)

df_market_pnl['pnl_cumulative'] = df_market_pnl.groupby('asset')['pnl'].cumsum()
df_market_pnl['feesPaid_cumulative'] = df_market_pnl.groupby('asset')['feesPaid'].cumsum()
df_market_pnl['netPnl_cumulative'] = df_market_pnl.groupby('asset')['netPnl'].cumsum()



In [56]:
fig = px.line(
    df_market_pnl,
    x='timestamp',
    y='pnl_cumulative',
    color='asset'
)
fig.show()

In [57]:
fig = px.line(
    df_market_pnl,
    x='timestamp',
    y='netPnl_cumulative',
    color='asset'
)
fig.show()


In [58]:
fig = px.line(
    df_market_pnl,
    x='timestamp',
    y='feesPaid_cumulative',
    color='asset'
)
fig.show()


In [59]:
df_market_pnl.to_csv('output/market_cumulative_pnl.csv', index=False)

In [60]:
df_market_pnl.groupby('asset')['netPnl'].sum().sort_values().reset_index().to_csv('output/market_pnl.csv', index=False)

## Do the same with position data

In [61]:
df_position_pnl = df_position[df_position['isOpen'] == False].sort_values(['asset', 'closeTimestamp'])
df_position_pnl['netPnl'] = df_position_pnl['pnl'] - df_position_pnl['feesPaid']

df_position_pnl['closeTimestamp'] = df_position_pnl['closeTimestamp'].astype(np.int64)
df_position_pnl['pnl'] = df_position_pnl['pnl'].astype(np.float64)
df_position_pnl['netPnl'] = df_position_pnl['netPnl'].astype(np.float64)
df_position_pnl['netFunding'] = df_position_pnl['netFunding'].astype(np.float64)

df_position_pnl['pnl_cumulative'] = df_position_pnl.groupby('asset')['pnl'].cumsum()
df_position_pnl['netPnl_cumulative'] = df_position_pnl.groupby('asset')['netPnl'].cumsum()
df_position_pnl['netFunding_cumulative'] = df_position_pnl.groupby('asset')['netFunding'].cumsum()



In [62]:
fig = px.line(
    df_position_pnl,
    x='closeTimestamp',
    y='pnl_cumulative',
    color='asset'
)
fig.show()


In [63]:
fig = px.line(
    df_position_pnl,
    x='closeTimestamp',
    y='netPnl_cumulative',
    color='asset'
)
fig.show()


In [64]:
fig = px.line(
    df_position_pnl,
    x='closeTimestamp',
    y='netFunding_cumulative',
    color='asset'
)
fig.show()


In [65]:
df_position_pnl['netPnl'].sum()

-1094740.9451364018

In [66]:
df_position_pnl[df_position_pnl['asset'] == 'ATOM']['closeTimestamp'].min()

1675894747